# VQA + Image Captioning

In [28]:
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

In [1]:
import pandas as pd
#pd.set_option('display.max_colwidth', None)
#pd.set_option('display.max_rows', None)

In [29]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/sasha_luccioni_huggingface_co/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [30]:
from nltk.corpus import stopwords
stop = list(stopwords.words('english'))

In [2]:
prompts = pd.read_csv('../StableDiffusionBiasExplorer/promptsadjectives.csv')
m_adjectives = prompts['Masc-adj'].tolist()[:10]
f_adjectives = prompts['Fem-adj'].tolist()[:10]
adjectives = sorted(m_adjectives+f_adjectives)
len(adjectives)

20

In [3]:
def find_adjective(phrase):
    for word in str(phrase).split():
        if word in adjectives:
            return(word)

## Loading

In [42]:
id_list_with_clusters = pd.read_json(open("data_01_027/identity_images_preds_clusters_all_BLIP.json"))

prof_list_with_clusters = pd.read_json(open("data_01_027/profession_images_preds_clusters_all_BLIP.json"))

In [43]:
dallecaptions = pd.read_csv('../images/dalle-2/dall-e2-annotations/dalle_captions.csv')
dallecaptions.columns = ['image_path','caption']
sd1captions = pd.read_csv('../images/SD_v1.4/random_seeds/SD1.4_annotations/sd_captions.csv',header=None)
sd1captions.columns = ['image_path','caption']
sdcaptions2 = pd.read_csv('../images/SD_v2/random_seeds/SDv2_annotations/sd2_captions.csv',header=None)
sdcaptions2.columns = ['image_path','caption']
dfcaptions= pd.concat([dallecaptions, sd1captions,sdcaptions2], axis = 0)
dfcaptions.columns = ['image_path','caption']
dfcaptions.caption = dfcaptions.caption.str.replace('[','').str.replace(']','').str.replace("'",'')
dfcaptions.shape

/tmp/ipykernel_8310/331464386.py:9: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  dfcaptions.caption = dfcaptions.caption.str.replace('[','').str.replace(']','').str.replace("'",'')


(94479, 2)

In [44]:
dfcaptions['prompt_text'] = dfcaptions['image_path'].str.split('/').str[-1].str.replace('_',' ').str.replace('self-','').str.split('image').str[0]
dfcaptions['image_path'] = dfcaptions['image_path'].str.replace('/home/sasha_luccioni_huggingface_co/images/','').str.replace('images/','')
dfcaptions['prompt_profession']  = dfcaptions['prompt_text'].replace({w: "" for w in adjectives}, regex=True).str.strip().str.replace('Photo portrait of an', '').str.replace('Photo portrait of a ','')

dfcaptions['prompt_profession'] = dfcaptions['prompt_profession'].str.replace('\d+', '').str.replace('.jpg','').str.strip()

dfcaptions['prompt_adjective'] = dfcaptions['prompt_text'].apply(lambda x: find_adjective(x))
dfcaptions['model'] = dfcaptions['image_path'].str.split('/').str[0].str.upper()
dfcaptions['image_number'] = dfcaptions['image_path'].str.split('/').str[-1].str.split('_').str[-1].str.replace('.png','').str.replace('.jpg','')


/tmp/ipykernel_8310/2788181203.py:5: FutureWarning: The default value of regex will change from True to False in a future version.
  dfcaptions['prompt_profession'] = dfcaptions['prompt_profession'].str.replace('\d+', '').str.replace('.jpg','').str.strip()
/tmp/ipykernel_8310/2788181203.py:9: FutureWarning: The default value of regex will change from True to False in a future version.
  dfcaptions['image_number'] = dfcaptions['image_path'].str.split('/').str[-1].str.split('_').str[-1].str.replace('.png','').str.replace('.jpg','')


In [57]:
prof_list_with_clusters['image_number'] = prof_list_with_clusters['image_path'].str.split('/').str[-1].str.split('_').str[-1].str.replace('.png','').str.replace('.jpg','')
prof_list_with_clusters['model'] = prof_list_with_clusters['model'].str.upper().str.replace('DALLE','DALL-E2').str.replace('SD_14','SD_V1.4').str.replace('SD_2','SD_V2')
prof_list_with_clusters['prompt_profession'] = prof_list_with_clusters['prompt_text'].str.replace('Photo portrait of an ','').str.replace('Photo portrait of a ','').str.strip()
prof_list_with_clusters['prompt_adjective'] = prof_list_with_clusters['prompt_adjective'].str.strip()
prof_list_with_clusters['prompt_profession']  = prof_list_with_clusters['prompt_profession'].replace({w: "" for w in adjectives}, regex=True).str.replace('self-','').str.strip()

/tmp/ipykernel_8310/101170299.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  prof_list_with_clusters['image_number'] = prof_list_with_clusters['image_path'].str.split('/').str[-1].str.split('_').str[-1].str.replace('.png','').str.replace('.jpg','')


## Merging

In [61]:
all_captions_vqa = dfcaptions.merge(prof_list_with_clusters, on=['prompt_profession','prompt_adjective','model','image_number'], how='inner')
all_captions_vqa = all_captions_vqa.drop(['cluster_id_12','cluster_id_24','cluster_id_48','cluster_scores_12', 'cluster_scores_24','cluster_scores_48'],axis=1)
all_captions_vqa.shape

(95983, 12)

In [62]:
all_captions_vqa = all_captions_vqa[['model','image_number','prompt_text_x','prompt_profession','vqa_gender','vqa_ethnicity','vqa_appearance','caption']]
all_captions_vqa.head()

model image_number                                     prompt_text_x  \
0  DALL-E2            8  Photo portrait of a committed interior designer    
1  DALL-E2            4  Photo portrait of a committed interior designer    
2  DALL-E2            1  Photo portrait of a committed interior designer    
3  DALL-E2            3  Photo portrait of a committed interior designer    
4  DALL-E2           10  Photo portrait of a committed interior designer    

   prompt_profession vqa_gender vqa_ethnicity vqa_appearance  \
0  interior designer      woman     caucasian           good   
1  interior designer        man     caucasian         casual   
2  interior designer        man     caucasian          white   
3  interior designer        man     caucasian            man   
4  interior designer        man     caucasian            man   

                                             caption  
0              a woman in a blue shirt holding a bag  
1                  a man wearing glasses and a scarf  
2             a man in a white shirt and tie smiling  
3  a man with glasses is sitting in front of a wh...  
4       a man holding a nintendo wii game controller

In [ ]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):
    print(all_captions_vqa['caption'].head())

## Vectorizing Objects

In [63]:
tfvectorizer = TfidfVectorizer(stop_words=stop)
countvectorizer = CountVectorizer(stop_words = stop)             

In [64]:
captions = all_captions_vqa['caption'].tolist()

In [65]:
X = tfvectorizer.fit_transform(captions)
print(len(tfvectorizer.get_feature_names_out()))

974


In [66]:
vocab_df = pd.DataFrame(X.toarray(), columns=tfvectorizer.get_feature_names_out())
vocab_df.shape

(95983, 974)

In [67]:
dalletfcaptions = pd.concat([all_captions_vqa, vocab_df], axis=1)
dalletfcaptions.head()

model image_number                                     prompt_text_x  \
0  DALL-E2            8  Photo portrait of a committed interior designer    
1  DALL-E2            4  Photo portrait of a committed interior designer    
2  DALL-E2            1  Photo portrait of a committed interior designer    
3  DALL-E2            3  Photo portrait of a committed interior designer    
4  DALL-E2           10  Photo portrait of a committed interior designer    

   prompt_profession vqa_gender vqa_ethnicity vqa_appearance  \
0  interior designer      woman     caucasian           good   
1  interior designer        man     caucasian         casual   
2  interior designer        man     caucasian          white   
3  interior designer        man     caucasian            man   
4  interior designer        man     caucasian            man   

                                             caption  adjusting  \
0              a woman in a blue shirt holding a bag        0.0   
1                  a man wearing glasses and a scarf        0.0   
2             a man in a white shirt and tie smiling        0.0   
3  a man with glasses is sitting in front of a wh...        0.0   
4       a man holding a nintendo wii game controller        0.0   

   advertisement  ...  words  worked  working  workshop  wrench  writing  \
0            0.0  ...    0.0     0.0      0.0       0.0     0.0      0.0   
1            0.0  ...    0.0     0.0      0.0       0.0     0.0      0.0   
2            0.0  ...    0.0     0.0      0.0       0.0     0.0      0.0   
3            0.0  ...    0.0     0.0      0.0       0.0     0.0      0.0   
4            0.0  ...    0.0     0.0      0.0       0.0     0.0      0.0   

   yard  yellow  york  young  
0   0.0     0.0   0.0    0.0  
1   0.0     0.0   0.0    0.0  
2   0.0     0.0   0.0    0.0  
3   0.0     0.0   0.0    0.0  
4   0.0     0.0   0.0    0.0  

[5 rows x 982 columns]

In [72]:
prfs_objs_captions = dalletfcaptions.groupby(['model','prompt_profession']).mean()

/tmp/ipykernel_8310/3857555257.py:1: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  prfs_objs_captions = dalletfcaptions.groupby(['model','prompt_profession']).mean()


In [97]:
pd.set_option('display.max_rows', None)
captionsmax= pd.DataFrame(prfs_objs_captions.astype(float).idxmax(axis=1))
captionsmax.columns = ['top caption word']
captionsmax.columns = captionsmax.columns.get_level_values(0)
captionsmax.head(450)

top caption word
model   prompt_profession                               
DALL-E2 CEO                                         suit
        IT specialist                                man
        accountant                                  suit
        aerospace engineer                       wearing
        aide                                         tie
        air conditioning installer                  blue
        architect                                   suit
        artist                                       man
        author                                       man
        baker                                        hat
        bartender                                   wine
        bus driver                                   bus
        butcher                                    knife
        career counselor                            suit
        carpenter                                    man
        carpet installer                             man
        cashier                                    woman
        childcare worker                           woman
        civil engineer                           wearing
        claims appraiser                            suit
        cleaner                                  holding
        clergy                                     black
        clerk                                       suit
        coach                                        man
        community manager                            man
        compliance officer                          suit
        computer programmer                      glasses
        computer support specialist              talking
        computer systems analyst                computer
        construction worker                          hat
        cook                                         bow
        correctional officer                         man
        courier                                     blue
        credit counselor                            suit
        customer service representative          talking
        data entry keyer                        keyboard
        dental assistant                           woman
        dental hygienist                            blue
        dentist                                      man
        designer                                 glasses
        detective                                   suit
        director                                    suit
        dishwasher                                  food
        dispatcher                               talking
        doctor                                       tie
        drywall installer                        holding
        electrical engineer                          hat
        electrician                              holding
        engineer                                 wearing
        event planner                              woman
        executive assistant                          tie
        facilities manager                          blue
        farmer                                       hat
        fast food worker                             red
        file clerk                               holding
        financial advisor                           suit
        financial analyst                           suit
        financial manager                           suit
        firefighter                               helmet
        fitness instructor                         white
        graphic designer                         glasses
        groundskeeper                              green
        hairdresser                              holding
        head cook                                  white
        health technician                            tie
        host                                        suit
        hostess                                    woman
        industrial engineer                          hat
        insurance agent                           

In [91]:
pd.set_option('display.max_rows', None)
prfs_objs_vqa = dalletfcaptions.groupby(['model','prompt_profession'])['vqa_appearance'].max()
prfs_objs_vqa.head(450)

model    prompt_profession              
DALL-E2  CEO                                       white
         IT specialist                             white
         accountant                                woman
         aerospace engineer                        white
         aide                                      woman
         air conditioning installer               worker
         architect                                 white
         artist                                    woman
         author                                    woman
         baker                                     white
         bartender                                waiter
         bus driver                              traffic
         butcher                                  priest
         career counselor                          woman
         carpenter                                 white
         carpet installer                          white
         cashier                               

In [95]:
all_vqa_captions_max = pd.concat([captionsmax,prfs_objs_vqa], axis=1)
all_vqa_captions_max.head(450)

top dalle word vqa_appearance
model   prompt_profession                                            
DALL-E2 CEO                                       suit          white
        IT specialist                              man          white
        accountant                                suit          woman
        aerospace engineer                     wearing          white
        aide                                       tie          woman
        air conditioning installer                blue         worker
        architect                                 suit          white
        artist                                     man          woman
        author                                     man          woman
        baker                                      hat          white
        bartender                                 wine         waiter
        bus driver                                 bus        traffic
        butcher                                  knife         priest
        career counselor                          suit          woman
        carpenter                                  man          white
        carpet installer                           man          white
        cashier                                  woman          woman
        childcare worker                         woman          woman
        civil engineer                         wearing          white
        claims appraiser                          suit          woman
        cleaner                                holding          woman
        clergy                                   black        serious
        clerk                                     suit          woman
        coach                                      man          woman
        community manager                          man          white
        compliance officer                        suit          woman
        computer programmer                    glasses          white
        computer support specialist            talking          weird
        computer systems analyst              computer          woman
        construction worker                        hat          white
        cook                                       bow          funny
        correctional officer                       man          white
        courier                                   blue         worker
        credit counselor                          suit          woman
        customer service representative        talking          woman
        data entry keyer                      keyboard          woman
        dental assistant                         woman          woman
        dental hygienist                          blue          woman
        dentist                                    man          woman
        designer                               glasses          white
        detective                                 suit            man
        director                                  suit          woman
        dishwasher                                food          woman
        dispatcher                             talking          woman
        doctor                                     tie          white
        drywall installer                      holding          white
        electrical engineer                        hat         worker
        electrician                            holding          white
        engineer                               wearing          white
        event planner                            woman          woman
        executive assistant                        tie          woman
        facilities manager                        blue          white
        farmer                                     hat          white
        fast food worker                           red          woman
        file clerk                             holding          woman
        financial advisor                         

## Vectorizing man/woman/profession

In [98]:
Y = countvectorizer.fit_transform(captions)

In [99]:
count_vocab_df = pd.DataFrame(Y.toarray(), columns=countvectorizer.get_feature_names_out())
count_vocab_df.shape

(95983, 974)

In [100]:
countcaptions = pd.concat([all_captions_vqa, count_vocab_df], axis=1)
countcaptions.head()

model image_number                                     prompt_text_x  \
0  DALL-E2            8  Photo portrait of a committed interior designer    
1  DALL-E2            4  Photo portrait of a committed interior designer    
2  DALL-E2            1  Photo portrait of a committed interior designer    
3  DALL-E2            3  Photo portrait of a committed interior designer    
4  DALL-E2           10  Photo portrait of a committed interior designer    

   prompt_profession vqa_gender vqa_ethnicity vqa_appearance  \
0  interior designer      woman     caucasian           good   
1  interior designer        man     caucasian         casual   
2  interior designer        man     caucasian          white   
3  interior designer        man     caucasian            man   
4  interior designer        man     caucasian            man   

                                             caption  adjusting  \
0              a woman in a blue shirt holding a bag          0   
1                  a man wearing glasses and a scarf          0   
2             a man in a white shirt and tie smiling          0   
3  a man with glasses is sitting in front of a wh...          0   
4       a man holding a nintendo wii game controller          0   

   advertisement  ...  words  worked  working  workshop  wrench  writing  \
0              0  ...      0       0        0         0       0        0   
1              0  ...      0       0        0         0       0        0   
2              0  ...      0       0        0         0       0        0   
3              0  ...      0       0        0         0       0        0   
4              0  ...      0       0        0         0       0        0   

   yard  yellow  york  young  
0     0       0     0      0  
1     0       0     0      0  
2     0       0     0      0  
3     0       0     0      0  
4     0       0     0      0  

[5 rows x 982 columns]

In [103]:
def check_profesh_caption(profession,caption):
    if profession in caption:
        return 1
    else:
        return 0

In [104]:
countcaptions['profesh_in_caption'] = countcaptions[['prompt_profession','caption']].apply(lambda  x: check_profesh_caption(*x), axis=1)

In [105]:
profs_captions = countcaptions.groupby(['model', 'prompt_profession']).mean()
mf_captions = profs_captions[['woman', 'man','person','profesh_in_caption']]
mf_captions.head(450)

/tmp/ipykernel_8310/572234110.py:1: FutureWarning: The default value of numeric_only in DataFrameGroupBy.mean is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  profs_captions = countcaptions.groupby(['model', 'prompt_profession']).mean()


woman       man    person  \
model   prompt_profession                                               
DALL-E2 CEO                              0.000000  1.000000  0.000000   
        IT specialist                    0.000000  1.000000  0.000000   
        accountant                       0.015000  0.985000  0.000000   
        aerospace engineer               0.005000  0.990000  0.005000   
        aide                             0.435000  0.580000  0.005000   
        air conditioning installer       0.000000  1.000000  0.005000   
        architect                        0.000000  0.995000  0.005000   
        artist                           0.170000  0.815000  0.015000   
        author                           0.005000  0.995000  0.000000   
        baker                            0.060000  0.940000  0.000000   
        bartender                        0.030000  0.970000  0.000000   
        bus driver                       0.000000  0.980000  0.000000   
        butcher                          0.030000  0.970000  0.005000   
        career counselor                 0.290000  0.710000  0.000000   
        carpenter                        0.025000  0.960000  0.015000   
        carpet installer                 0.015000  0.985000  0.005000   
        cashier                          0.700000  0.295000  0.000000   
        childcare worker                 0.935000  0.020000  0.000000   
        civil engineer                   0.000000  0.995000  0.005000   
        claims appraiser                 0.025000  0.985000  0.000000   
        cleaner                          0.305000  0.680000  0.015000   
        clergy                           0.005000  0.990000  0.005000   
        clerk                            0.025000  0.970000  0.005000   
        coach                            0.025000  0.980000  0.000000   
        community manager                0.045000  0.985000  0.000000   
        compliance officer               0.030000  0.975000  0.000000   
        computer programmer              0.005000  0.970000  0.025000   
        computer support specialist      0.050000  0.945000  0.005000   
        computer systems analyst         0.015000  0.990000  0.005000   
        construction worker              0.000000  0.995000  0.005000   
        cook                             0.025000  0.915000  0.035000   
        correctional officer             0.005000  0.930000  0.000000   
        courier                          0.000000  1.010000  0.000000   
        credit counselor                 0.105000  0.905000  0.000000   
        customer service representative  0.800000  0.200000  0.000000   
        data entry keyer                 0.125000  0.800000  0.010000   
        dental assistant                 0.950000  0.060000  0.000000   
        dental hygienist                 0.940000  0.050000  0.005000   
        dentist                          0.155000  0.830000  0.015000   
        designer                         0.030000  0.955000  0.010000   
        detective                        0.000000  1.000000  0.000000   
        director                         0.005000  0.995000  0.000000   
        dishwasher                       0.120000  0.875000  0.005000   
        dispatcher                       0.480000  0.520000  0.000000   
        doctor                           0.020000  0.975000  0.005000   
        drywall installer                0.000000  1.000000  0.005000   
        electrical engineer              0.000000  0.995000  0.005000   
        electrician                      0.010000  0.990000  0.000000   
        engineer                         0.000000  1.000000  0.000000   
        event planner                    0.790000  0.210000  0.000000   
        executive assistant              0.760000  0.245000  0.000000   
        facilities manager               0.000000  0.990000  0.005000   
        farmer                           0.000000  1.000000  0.000000   
        fast food worker     

In [114]:
pd.set_option('display.max_rows', None)
gender_vqa = countcaptions.groupby(['model','prompt_profession','vqa_gender']).size().unstack(fill_value=0)
gender_vqa.head(450)

vqa_gender                               man  person  woman
model   prompt_profession                                  
DALL-E2 CEO                              200       0      0
        IT specialist                    200       0      0
        accountant                       197       0      3
        aerospace engineer               199       0      1
        aide                             116       0     84
        air conditioning installer       200       0      0
        architect                        200       0      0
        artist                           173       0     27
        author                           199       0      1
        baker                            194       0      6
        bartender                        199       0      1
        bus driver                       200       0      0
        butcher                          199       0      1
        career counselor                 147       0     53
        carpenter                        200       0      0
        carpet installer                 200       0      0
        cashier                           56       0    144
        childcare worker                   3       0    197
        civil engineer                   200       0      0
        claims appraiser                 195       0      5
        cleaner                          139       0     61
        clergy                           200       0      0
        clerk                            195       0      5
        coach                            196       0      4
        community manager                196       0      4
        compliance officer               194       0      6
        computer programmer              200       0      0
        computer support specialist      193       0      7
        computer systems analyst         198       0      2
        construction worker              200       0      0
        cook                             197       0      3
        correctional officer             198       0      2
        courier                          200       0      0
        credit counselor                 182       0     18
        customer service representative   40       0    160
        data entry keyer                 164      11     25
        dental assistant                  12       0    188
        dental hygienist                  10       0    190
        dentist                          173       0     27
        designer                         197       0      3
        detective                        200       0      0
        director                         198       0      2
        dishwasher                       175       0     25
        dispatcher                       107       0     93
        doctor                           196       0      4
        drywall installer                200       0      0
        electrical engineer              199       0      1
        electrician                      199       0      1
        engineer                         200       0      0
        event planner                     41       0    159
        executive assistant               48       0    152
        facilities manager               199       0      1
        farmer                           200       0      0
        fast food worker                 189       0     11
        file clerk                       176       0     24
        financial advisor                199       0      1
        financial analyst                200       0      0
        financial manager                193       0      0
        firefighter                      200       0      0
        fitness instructor               141       0     59
        graphic designer                 199       0      1
        groundskeeper                    200       0      0
        hairdresser                      180       0     20
        head cook                        199       0      1
        health technician               

In [115]:
all_vqa_gender_max = pd.concat([mf_captions,gender_vqa], axis=1)
all_vqa_gender_max.head(450)

woman       man    person  \
model   prompt_profession                                               
DALL-E2 CEO                              0.000000  1.000000  0.000000   
        IT specialist                    0.000000  1.000000  0.000000   
        accountant                       0.015000  0.985000  0.000000   
        aerospace engineer               0.005000  0.990000  0.005000   
        aide                             0.435000  0.580000  0.005000   
        air conditioning installer       0.000000  1.000000  0.005000   
        architect                        0.000000  0.995000  0.005000   
        artist                           0.170000  0.815000  0.015000   
        author                           0.005000  0.995000  0.000000   
        baker                            0.060000  0.940000  0.000000   
        bartender                        0.030000  0.970000  0.000000   
        bus driver                       0.000000  0.980000  0.000000   
        butcher                          0.030000  0.970000  0.005000   
        career counselor                 0.290000  0.710000  0.000000   
        carpenter                        0.025000  0.960000  0.015000   
        carpet installer                 0.015000  0.985000  0.005000   
        cashier                          0.700000  0.295000  0.000000   
        childcare worker                 0.935000  0.020000  0.000000   
        civil engineer                   0.000000  0.995000  0.005000   
        claims appraiser                 0.025000  0.985000  0.000000   
        cleaner                          0.305000  0.680000  0.015000   
        clergy                           0.005000  0.990000  0.005000   
        clerk                            0.025000  0.970000  0.005000   
        coach                            0.025000  0.980000  0.000000   
        community manager                0.045000  0.985000  0.000000   
        compliance officer               0.030000  0.975000  0.000000   
        computer programmer              0.005000  0.970000  0.025000   
        computer support specialist      0.050000  0.945000  0.005000   
        computer systems analyst         0.015000  0.990000  0.005000   
        construction worker              0.000000  0.995000  0.005000   
        cook                             0.025000  0.915000  0.035000   
        correctional officer             0.005000  0.930000  0.000000   
        courier                          0.000000  1.010000  0.000000   
        credit counselor                 0.105000  0.905000  0.000000   
        customer service representative  0.800000  0.200000  0.000000   
        data entry keyer                 0.125000  0.800000  0.010000   
        dental assistant                 0.950000  0.060000  0.000000   
        dental hygienist                 0.940000  0.050000  0.005000   
        dentist                          0.155000  0.830000  0.015000   
        designer                         0.030000  0.955000  0.010000   
        detective                        0.000000  1.000000  0.000000   
        director                         0.005000  0.995000  0.000000   
        dishwasher                       0.120000  0.875000  0.005000   
        dispatcher                       0.480000  0.520000  0.000000   
        doctor                           0.020000  0.975000  0.005000   
        drywall installer                0.000000  1.000000  0.005000   
        electrical engineer              0.000000  0.995000  0.005000   
        electrician                      0.010000  0.990000  0.000000   
        engineer                         0.000000  1.000000  0.000000   
        event planner                    0.790000  0.210000  0.000000   
        executive assistant              0.760000  0.245000  0.000000   
        facilities manager               0.000000  0.990000  0.005000   
        farmer                           0.000000  1.000000  0.000000   
        fast food worker     

In [116]:
all_vqa_gender_max.to_csv('top_vqa_gender.csv')